### Import Dataset

In [1]:
import pandas as pd
import numpy as np
import psycopg2

/Users/apple/venv/lib/python3.6/site-packages/psycopg2/__init__.py:144: UserWarning: The psycopg2 wheel package will be renamed from release 2.8; in order to keep installing from binary please use "pip install psycopg2-binary" instead. For details see: <http://initd.org/psycopg/docs/install.html#binary-install-from-pypi>.
  """)


In [2]:
df =  pd.read_excel('commit data.xlsx')
print(df.head())
print(df.shape)

  commit id class
0   0b9ea98   NFT
1   980d9f8   RFT
2   e9d5060   NFT
3   a63639b   NFT
4   a611d64   RMN
(926, 2)


### Connect Database

In [5]:
try:
    conn =  psycopg2.connect("dbname='squad' user='apple' password = 'mst123456' host='localhost'")
except:
    print ("I am unable to connect to the database")  

cur = conn.cursor()

csha_list = df['commit id'].values
print(csha_list[0])
print(csha_list[96])

commit_message = []
for index, csha in enumerate(csha_list):
    qr =  "SELECT message FROM commits WHERE csha LIKE '{}%'".format(csha_list[index].strip())
    cur.execute(qr)
    fetched_row = cur.fetchone()
    if fetched_row != None:
        if index < 20:
            print(index, fetched_row[0])
        commit_message.append(fetched_row[0])
    else:
        if index < 20:
            print('None')
        commit_message.append('None')

df['commit_message'] = commit_message
df.head()

0b9ea98
9dcf08d
0 [CALCITE-1124] Add TIMESTAMPADD, TIMESTAMPDIFF functions (Arina Ielchiieva)

Close apache/calcite#204

1 Move code from JdbcImplementor and JdbcRules to new class SqlImplementor

2 [CALCITE-968] Stream-to-relation and stream-to-stream joins (Milinda Pathirage)

Rule to transform Delta(Scan(constant-table)) to Empty;
fix NullPointerException in PruneEmptyRules.

3 [CALCITE-912] Add Avatica OpenConnectionRequest (Bruno Dumon)

Goal: passing of connection properties (the 'info') from the remote
avatica driver to the corresponding server-side connection.

Changes include:
 * in Meta: explicit opening of connections: there is a new
   openConnection() call. Client decides on the connection id.
   Implicit creation of unknown connections is gone.
 * JdbcMeta: default connection is gone, all methods have been
   extended with a connection id.
 * correspondingly, the various Service.Request's now carry a
   connection id (will make fixing CALCITE-871 easy)
 * (unrelated, but 

commit id class                                     commit_message
0   0b9ea98   NFT  [CALCITE-1124] Add TIMESTAMPADD, TIMESTAMPDIFF...
1   980d9f8   RFT  Move code from JdbcImplementor and JdbcRules t...
2   e9d5060   NFT  [CALCITE-968] Stream-to-relation and stream-to...
3   a63639b   NFT  [CALCITE-912] Add Avatica OpenConnectionReques...
4   a611d64   RMN  [CALCITE-296] Re-organize package structure;\n...

### Message Preprocessing

In [6]:
import nltk
nltk.download('stopwords')
nltk.download('words')
nltk.download('wordnet')
from nltk.corpus import stopwords
from ast import literal_eval
import re

[nltk_data] Downloading package stopwords to /Users/apple/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package words to /Users/apple/nltk_data...
[nltk_data]   Package words is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/apple/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


##### (i) Remove git-svn-id: 
e.g. git-svn-id: https://svn.apache.org/repos/asf/commons/proper/collections/trunk@1492866 13f79535-47bb-0310-9956-ffa450edef68

##### (ii) Remove Issue Number : e.g. [CALCITE-968]  [COMPRESS-392]

##### (iii) Remove Created by MOE - 
eg. Created by MOE: https://github.com/google/moe
MOE_MIGRATED_REVID=160142836

##### (iv) Remove Developer name
e.g. 344 [] User-defined aggregate functions with more than one parameter (hzyuemeng1)

##### (v) Remove http and email address

##### (vi) Other filter

- Authors
- Reviewers
- [...]
- digitial
- special character

#### Summary of all Filter

In [7]:
GIT_SVN_RE = re.compile('git-svn-id:.*\n')
issue_number_re = re.compile('[A-Za-z]+[-]\d+')
created_by_moe = re.compile('Created by MOE:.*\n')
MOE_ID = re.compile('MOE_MIGRATED_REVID=.*\n')
developer_name_re = re.compile('\(.*\)\n')
HTTP_RE = re.compile('(http|https):.*\n')
EMAIL_RE = re.compile('[a-zA-Z0-9]+@[a-zA-Z0-9]+\.[a-zA-Z0-9-.]+')
Other_RE = re.compile('(Author|Authors|Reviewers|Reviewer).*\n')
Bracket_RE = re.compile('\[.*\]')

break_line_re = re.compile('\n')
digital = re.compile('[0-9]')
BAD_SYMBOLS_RE = re.compile('[^0-9a-z ]')
STOPWORDS = set(stopwords.words('english'))

def text_prepare(text):
    """
        text: a string
        
        return: modified initial string
    """
    text = GIT_SVN_RE.sub('',text)
    text = issue_number_re.sub('',text)
    text = created_by_moe.sub('',text)
    text = MOE_ID.sub('',text)
    text = developer_name_re.sub('\n', text)
    text = HTTP_RE.sub('\n', text)
    text = EMAIL_RE.sub('\n',text)
    text = Other_RE.sub('', text)
    text = Bracket_RE.sub('', text)
    
    text = text.lower() # lowercase text
    text = break_line_re.sub(' ',text) # remove all \n
    text = digital.sub('',text)
    text = BAD_SYMBOLS_RE.sub('', text) # delete symbols which are in BAD_SYMBOLS_RE from text
    
    text = ' '.join([x for x in text.split() if x and x not in STOPWORDS]) # delete stopwords from text
    return text

In [8]:
print('====================================================')
test_commit = df['commit_message'].values[232]
print(test_commit)
test_commit = text_prepare(test_commit)
print(test_commit)

print('====================================================')
df['commit_message'] = [text_prepare(line) for line in df['commit_message']]
for index, line in enumerate(df['commit_message'].values):
    if index < 10:
        print(index, line)

Reconcile the cancellation semantics for Futures.combine, successfulAsList, allAsList, and withFallback to be consistent with Futures.transform.  Now, all cancellations are back-propagated to the input futures.  We also expose the interruption state in AbstractFuture with a protected method.  To ensure the interruption state is correct and threadsafe, we add an additional state to AbstractFuture's inner Sync class to atomically distinguish between cancelled and interrupted.
-------------
Created by MOE: http://code.google.com/p/moe-java
MOE_MIGRATED_REVID=33468640

reconcile cancellation semantics futurescombine successfulaslist allaslist withfallback consistent futurestransform cancellations backpropagated input futures also expose interruption state abstractfuture protected method ensure interruption state correct threadsafe add additional state abstractfutures inner sync class atomically distinguish cancelled interrupted
0 add timestampadd timestampdiff functions close apachecalcite

### Spell Checking - Handling wrong words

Three Options:
1. keep all wrong words
2. remove all wrong words
3. replace wrong words with some new words

In [78]:
!pip install pyenchant

In [9]:
from enchant.checker import SpellChecker
chkr = SpellChecker("en_US")
wrong_words = []
for index, text in enumerate(df['commit_message']):
    chkr.set_text(text)
    for err in chkr:
        if err.word not in wrong_words:
            wrong_words.append(err.word)
        #   print(index, err.word)

def remove_noise_words(message_array):
    res = []
    for text in message_array:
        text = ' '.join([x for x in text.split() if x and x not in wrong_words])
        res.append(text)
    return res

def replace_nosie_words_with_sth(message_array):
    res = []
    for text in message_array:
        # replace wrong word with something
        new_text = []
        for x in text.split():
            if x and x in wrong_words:
                new_text.append('something')
            else:
                new_text.append(x)
                
        text = ' '.join(new_text)
        res.append(text)
    return res

In [10]:
remove_noise_message = remove_noise_words(df['commit_message'].values)
for index, line in enumerate(remove_noise_message):
    if index < 10:
        print(index, line)

0 add functions close
1 move code new class
2 joins rule transform empty fix
3 add goal passing connection properties info remote driver corresponding connection changes include meta explicit opening connections new call client decides connection id implicit creation unknown connections gone default connection gone methods extended connection id correspondingly various carry connection id unrelated useful testing meaningful error messages remote driver
4 reorganize package structure naming convention planner rules change renames files deletes obsolete files content changes
5 infer collation project using monotonicity close
6 add piglet subset pig top calcite algebra includes parser distinct order limit group commands incomplete nested command add tests based examples reference
7 revert changes introduced rev particular means package coordinates changed back furthermore maven coordinates changes back
8 move methods correct class
9 bug select instructions implement instead


In [11]:
replaced_message = replace_nosie_words_with_sth(df['commit_message'].values)
for index, line in enumerate(replaced_message):
    if index < 10:
        print(index, line)

0 add something something functions close something
1 move code something something new class something
2 something something joins rule transform something empty fix something something
3 add something something goal passing connection properties info remote something driver corresponding something connection changes include meta explicit opening connections new something call client decides connection id implicit creation unknown connections gone something default connection gone methods extended connection id correspondingly various something carry connection id unrelated useful testing meaningful error messages remote driver
4 reorganize package structure naming convention planner rules change renames files deletes obsolete files content changes
5 infer collation project using monotonicity close something
6 add piglet subset pig something top calcite algebra includes parser distinct order limit group commands incomplete nested something command add tests based examples something re

In [13]:
original_commit_message = np.copy(df['commit_message'])
df['commit_message'] = remove_noise_message

### Word Stemming

In [14]:
from nltk.stem import SnowballStemmer
stemmer = SnowballStemmer("english") # Choose a language
# stemmer.stem("countries")
for index, text in enumerate(df['commit_message']):
#     print(index, df['cmt_msg'][index])
    df['commit_message'][index] = ' '.join([stemmer.stem(x) for x in text.split()])
#     print(index, df['cmt_msg'][index])

### Keywords Distribution

In [15]:
from scipy import sparse as sp_sparse
from sklearn.feature_extraction.text import TfidfVectorizer
from collections import Counter

In [16]:
words_counts = Counter()

for words in remove_noise_message:
    for word in words.split():
        words_counts[word] += 1

most_common_words_without_noise = sorted(words_counts.items(), key=lambda x: x[1], reverse=True)[:20]

print('Most common words total:')
for word in most_common_words_without_noise:
    print(word)

Most common words total:
('add', 125)
('fix', 95)
('added', 79)
('use', 74)
('code', 67)
('methods', 62)
('support', 61)
('method', 59)
('remove', 58)
('test', 50)
('new', 48)
('change', 47)
('fixed', 47)
('classes', 41)
('class', 40)
('make', 40)
('type', 33)
('changes', 32)
('comments', 32)
('used', 32)


In [142]:
tags_counts = Counter()
for tags in df['class'].values:
    tags_counts[tags] += 1
most_common_tags = sorted(tags_counts.items(), key=lambda x: x[1], reverse=True)[:]
most_common_tags

[('NFT', 276),
 ('FIX', 193),
 ('MOD', 156),
 ('DOC', 53),
 ('RFT', 43),
 ('DEL', 41),
 ('RMN', 37),
 ('CLN', 31),
 ('VER', 25),
 ('DPD', 21),
 ('ANT', 17),
 ('CMT', 15),
 ('TST', 7),
 ('IMP', 6),
 ('BRC', 4),
 ('MDL', 1)]

In [140]:
classes_ = df['class'].value_counts().index
print(classes_)

Index(['NFT', 'FIX', 'MOD', 'DOC', 'RFT', 'DEL', 'RMN', 'CLN', 'VER', 'DPD',
       'ANT', 'CMT', 'TST', 'IMP', 'BRC', 'MDL'],
      dtype='object')


In [74]:
custom_words_list = ['patch', 'hbase', 'checksum', 'code', 'version', 'byte', 'data', 'hfile', 'region', 'schedul', 'singl', 'can',
                'yarn', 'contribut', 'commit', 'merg', 'make', 'trunk', 'hadoop', 'svn', 'ignoreancestri', 'node', 'also', 
                'client', 'hdfs', 'mapreduc', 'lipcon', 'idea', 'common', 'file', 'ideadev', 'plugin', 'project', 'modul', 
                'find', 'border', 'addit', 'changeutilencod', 'clickabl', 'color', 'column', 'cach', 'jbrule', 'drool', 'coprocessor', 'regionserv', 
                'scan', 'resourcemanag', 'cherri', 'gong', 'ryza', 'sandi', 'xuan', 'token', 'contain', 'shen', 'todd', 'zhiji', 'tan', 
                'wangda', 'timelin', 'app', 'kasha', 'kashacherri', 'messag', 'spr', 'camel', 'http', 'now', 'class', 'default', 
                'pick', 'via']
custom_words_set = set(custom_words_list)
classes_ = df['class'].value_counts().index
most_frequent_words_cat = dict()
word_counter_dict = dict()

for cl in classes_:
    print("========================================================================")
    print(cl)
    commit_messages_cl = df[df['class'] == cl]['commit_message'].values
    
    words_counts = Counter()
    
    for words in commit_messages_cl:
        hash_dict = dict()
        for word in words.split():
            if word not in hash_dict and custom_words_set:  # remove VCS words in boosting paper 
                hash_dict[word] = True
                words_counts[word] += 1
            else:
                pass
    
    most_common_words = sorted(words_counts.items(), key=lambda x: x[1], reverse=True)[:-1]
    most_frequent_words_cat[cl] = most_common_words
    word_counter_dict[cl] = words_counts
    
    for index, word in enumerate(most_common_words):
        if index < 10:
            print(word)

NFT
('add', 77)
('use', 43)
('support', 41)
('ad', 32)
('implement', 30)
('method', 29)
('chang', 24)
('allow', 18)
('code', 17)
('new', 16)
FIX
('fix', 80)
('use', 28)
('chang', 18)
('test', 15)
('set', 14)
('bug', 13)
('method', 13)
('call', 13)
('avoid', 13)
('error', 13)
MOD
('use', 32)
('chang', 19)
('improv', 16)
('make', 16)
('method', 15)
('class', 12)
('implement', 11)
('remov', 11)
('list', 10)
('type', 10)
DOC
('fix', 13)
('add', 7)
('ad', 6)
('use', 5)
('move', 5)
('comment', 4)
('sinc', 4)
('miss', 4)
('tag', 4)
('licens', 3)
RFT
('move', 14)
('class', 10)
('method', 9)
('updat', 8)
('code', 7)
('remov', 5)
('test', 5)
('separ', 5)
('ad', 4)
('simplifi', 4)
DEL
('remov', 24)
('code', 8)
('deprec', 7)
('method', 6)
('delet', 6)
('class', 6)
('replac', 3)
('new', 3)
('relat', 3)
('use', 3)
RMN
('renam', 15)
('fix', 7)
('name', 4)
('method', 4)
('remov', 4)
('packag', 3)
('trail', 3)
('space', 3)
('line', 3)
('format', 3)
CLN
('remov', 19)
('code', 8)
('cleanup', 7)
('method'

In [85]:
def get_class_length(dictionary_obj):
    '''
    return:  returns dictionary with class lengths 
    '''
    class_length = dict()  # length of dictionary values in most_frequent_words_cat 
    for key, vals in dictionary_obj.items(): 
        count = 0
        for val in vals: 
            count += 1 
        class_length[key] = count
    return class_length 

# smallest class 'MDL'
get_class_length(most_frequent_words_cat)

{'NFT': 832,
 'FIX': 735,
 'MOD': 619,
 'DOC': 135,
 'RFT': 148,
 'DEL': 170,
 'RMN': 85,
 'CLN': 206,
 'VER': 98,
 'DPD': 78,
 'ANT': 75,
 'CMT': 74,
 'TST': 46,
 'IMP': 9,
 'BRC': 41,
 'MDL': 1}

In [76]:
def make_keywords_features(threshold, most_frequent_words_cat):
    
    print('=================================================')
    temp_list_dict = dict()
    for key, vals in most_frequent_words_cat.items(): 
        temp_list = []
        if len(vals) > threshold: 
            temp_list = vals[:threshold]
        else:
            temp_list = vals 
        temp_list_dict[key] = temp_list
    
    class_length = get_class_length(temp_list_dict)
    for key, val in class_length.items(): 
        print(key, val)
        
    print('=================================================')
    temp_list = []
    for key, vals in temp_list_dict.items(): 
        for val, _ in vals: 
            temp_list.append(val)
    unique_keywords_words_cat = set(temp_list)
    print(len(unique_keywords_words_cat))
    print(" ")

    for index, val in enumerate(unique_keywords_words_cat):
        if index < 30:
            print(val)
            
    print('=================================================')
    unique_keywords_words_cat = list(unique_keywords_words_cat)
    key_words_features_dict = dict()
    for val in unique_keywords_words_cat: 
        key_words_features_dict[val] = unique_keywords_words_cat.index(val)

    # build keywords features
    key_words_features = np.zeros((926, len(unique_keywords_words_cat)))

    # fill in numpy array
    for idx, commit in enumerate(df['commit_message'].values): 
        commit = commit.split()
        for word in commit: 
            if word in key_words_features_dict.keys(): 
                key_words_features[idx, key_words_features_dict[word]] = 1
    np.set_printoptions(precision=2)
    print(key_words_features[1, :])
    
    return key_words_features   

In [83]:
threshold = 1000 # threshold for the number of keywords
key_words_features = make_keywords_features(threshold, most_frequent_words_cat)

NFT 832
FIX 735
MOD 619
DOC 135
RFT 148
DEL 170
RMN 85
CLN 206
VER 98
DPD 78
ANT 75
CMT 74
TST 46
IMP 9
BRC 41
MDL 1
1427
 
circumst
drop
output
prod
cpl
substitut
wrap
minimum
wire
round
record
repli
inform
licens
problem
merg
distribut
effici
inconsist
space
build
substr
apach
devic
compress
integr
print
regist
bound
item
[0. 0. 0. ... 0. 0. 0.]


### Machine learing model

#### Decision Tree

In [97]:
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import GridSearchCV


X = key_words_features
y = df['class'].values
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.15, random_state=42)

classifier = DecisionTreeClassifier(random_state=42, class_weight = 'balanced')

param_grid = {'max_depth': [1, 5, 10, 20, 50, 100, 200, 500, 1000], 
              'min_samples_split': [0.5,1.0,5,10,20],
              'min_samples_leaf':[1,2,3,4,5],
              'min_weight_fraction_leaf': [0.0, 0.2,0.5],
            'max_features': [10,20,50,100,500,1000]
            }

clf = GridSearchCV(classifier, param_grid = param_grid, cv=StratifiedKFold(n_splits = 5) ,scoring='f1_micro', verbose=1000)

clf.fit(X_train, y_train)
y_pred = clf.predict(X_test) 
print(classification_report(y_test, y_pred))

Fitting 5 folds for each of 4050 candidates, totalling 20250 fits
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=0.5, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=0.5, min_weight_fraction_leaf=0.0, score=0.193, total=   0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=0.5, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=0.5, min_weight_fraction_leaf=0.0, score=0.038, total=   0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=0.5, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=0.5, min_weight_fractio

/Users/apple/venv/lib/python3.6/site-packages/sklearn/model_selection/_split.py:657: Warning: The least populated class in y has only 1 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)


[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=0.5, min_weight_fraction_leaf=0.5, score=0.052, total=   0.0s
[Parallel(n_jobs=1)]: Done  14 out of  14 | elapsed:    0.2s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=0.5, min_weight_fraction_leaf=0.5 
[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=0.5, min_weight_fraction_leaf=0.5, score=0.046, total=   0.0s
[Parallel(n_jobs=1)]: Done  15 out of  15 | elapsed:    0.2s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=1.0, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=1.0, min_weight_fraction_leaf=0.0, score=0.193, total=   0.0s
[Parallel(n_jobs=1)]: Done  16 out of  16 | elapsed:    0.2s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=1.0, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_featu

[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=5, min_weight_fraction_leaf=0.5, score=0.046, total=   0.0s
[Parallel(n_jobs=1)]: Done  45 out of  45 | elapsed:    0.6s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=10, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=10, min_weight_fraction_leaf=0.0, score=0.193, total=   0.0s
[Parallel(n_jobs=1)]: Done  46 out of  46 | elapsed:    0.7s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=10, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=10, min_weight_fraction_leaf=0.0, score=0.038, total=   0.0s
[Parallel(n_jobs=1)]: Done  47 out of  47 | elapsed:    0.7s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=10, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_features=10,

[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=20, min_weight_fraction_leaf=0.5, score=0.052, total=   0.0s
[Parallel(n_jobs=1)]: Done  74 out of  74 | elapsed:    1.3s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=20, min_weight_fraction_leaf=0.5 
[CV]  max_depth=1, max_features=10, min_samples_leaf=1, min_samples_split=20, min_weight_fraction_leaf=0.5, score=0.046, total=   0.0s
[Parallel(n_jobs=1)]: Done  75 out of  75 | elapsed:    1.3s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=2, min_samples_split=0.5, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_features=10, min_samples_leaf=2, min_samples_split=0.5, min_weight_fraction_leaf=0.0, score=0.193, total=   0.0s
[Parallel(n_jobs=1)]: Done  76 out of  76 | elapsed:    1.3s remaining:    0.0s
[CV] max_depth=1, max_features=10, min_samples_leaf=2, min_samples_split=0.5, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1, max_features

...

[CV]  max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=0.5, min_weight_fraction_leaf=0.5, score=0.308, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=0.5, min_weight_fraction_leaf=0.5 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=0.5, min_weight_fraction_leaf=0.5, score=0.052, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=0.5, min_weight_fraction_leaf=0.5 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=0.5, min_weight_fraction_leaf=0.5, score=0.046, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=1.0, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=1.0, min_weight_fraction_leaf=0.0, score=0.193, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=1.0, min_weight_fra

[CV]  max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=10, min_weight_fraction_leaf=0.0, score=0.192, total=   0.1s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=10, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=10, min_weight_fraction_leaf=0.0, score=0.201, total=   0.1s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=10, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=10, min_weight_fraction_leaf=0.0, score=0.197, total=   0.1s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=10, min_weight_fraction_leaf=0.2 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=10, min_weight_fraction_leaf=0.2, score=0.193, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=4, min_samples_split=10, min_weight_fraction_le

[CV]  max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=0.5, min_weight_fraction_leaf=0.5, score=0.038, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=0.5, min_weight_fraction_leaf=0.5 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=0.5, min_weight_fraction_leaf=0.5, score=0.308, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=0.5, min_weight_fraction_leaf=0.5 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=0.5, min_weight_fraction_leaf=0.5, score=0.052, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=0.5, min_weight_fraction_leaf=0.5 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=0.5, min_weight_fraction_leaf=0.5, score=0.046, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=1.0, min_weight_fra

[CV]  max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=10, min_weight_fraction_leaf=0.0, score=0.199, total=   0.1s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=10, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=10, min_weight_fraction_leaf=0.0, score=0.234, total=   0.1s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=10, min_weight_fraction_leaf=0.0 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=10, min_weight_fraction_leaf=0.0, score=0.191, total=   0.1s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=10, min_weight_fraction_leaf=0.2 
[CV]  max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=10, min_weight_fraction_leaf=0.2, score=0.193, total=   0.0s
[CV] max_depth=1000, max_features=1000, min_samples_leaf=5, min_samples_split=10, min_weight_fraction_le

/Users/apple/venv/lib/python3.6/site-packages/sklearn/model_selection/_search.py:813: DeprecationWarning: The default of the `iid` parameter will change from True to False in version 0.22 and will be removed in 0.24. This will change numeric results when test-set sizes are unequal.
  DeprecationWarning)
/Users/apple/venv/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


#### GBM

#### Random Forest

### Drop empty line

In [30]:
data = df[(df['commit_message']!='') | (df['commit_message']!='None')]
data = data.reset_index(drop=True)

### TD-IDF and Machine Learning

In [100]:
from scipy import sparse as sp_sparse
from sklearn.feature_extraction.text import TfidfVectorizer
from collections import Counter
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score
from sklearn.metrics import f1_score
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline

In [99]:
def tfidf_features(X):
    """
        X_train, X_val, X_test — samples        
        return TF-IDF vectorized representation of each sample and vocabulary
    """
    # Create TF-IDF vectorizer with a proper parameters choice
    # Fit the vectorizer on the train set
    # Transform the train, test, and val sets and return the result
    
    
    tfidf_vectorizer = TfidfVectorizer(min_df=6, max_df=0.2, ngram_range=(1, 2),token_pattern='(\S+)', max_features = 800)
    
    X = tfidf_vectorizer.fit_transform(X)
    
    return X,tfidf_vectorizer.vocabulary_

X, y = df['commit_message'].values, df['class'].values
X_tfidf, tfidf_vocab = tfidf_features(X)
tfidf_reversed_vocab = {i:word for word,i in tfidf_vocab.items()}
X_train, X_test, y_train, y_test = train_test_split(X_tfidf, y, test_size=0.20, random_state=42)

#### Logistic Regression

In [105]:
clf = LogisticRegression(random_state=0, solver='lbfgs', multi_class='multinomial').fit(X_train, y_train)

y_pre_test = clf.predict(X_test)
predictions = clf.predict_proba(X_test) 
print(clf.score(X_test, y_test))
print(f1_score(y_test, y_pre_test, average='macro'))

0.45698924731182794
0.21708503660672737


/Users/apple/venv/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


#### Logistic Regression with Regularization

In [137]:
X, y = df['commit_message'].values, df['class'].values
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=42)

tf_idf = TfidfVectorizer()
clf = LogisticRegression(random_state=0, solver='lbfgs', multi_class='multinomial')
#LogisticRegression(penalty='l1',random_state=0,solver='saga',max_iter=1000,multi_class='multinomial')

pipeline = Pipeline([('tfidf', tf_idf),('lr', clf)])

param_grid = {
              'tfidf__ngram_range':[(1,1),(1,2),(1, 3)],
              'tfidf__max_df':[0.2,0.5,0.8,1.0],
              'tfidf__min_df':[0.1],
              'tfidf__max_features':[50,100,200,500,None],
              'tfidf__binary':[True, False],
              'tfidf__norm':['l1','l2'],
              'tfidf__use_idf':[True, False],
              'tfidf__smooth_idf':[True, False],
              'tfidf__sublinear_tf':[True, False]
            }

clf = GridSearchCV(pipeline, param_grid = param_grid, cv=5 ,scoring='f1_micro', verbose = 1)

clf.fit(X_train, y_train)
y_pred = clf.predict(X_test) 
print(classification_report(y_test, y_pred))

best_parameters = clf.best_estimator_.get_params()
for param_name in sorted(param_grid.keys()):
    print("\t%s: %r" % (param_name, best_parameters[param_name]))

Fitting 5 folds for each of 1920 candidates, totalling 9600 fits


/Users/apple/venv/lib/python3.6/site-packages/sklearn/model_selection/_split.py:657: Warning: The least populated class in y has only 1 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


KeyboardInterrupt: 

#### Logsitic Regression One VS Rest Classifier

In [107]:
clf = LogisticRegression(random_state=0, solver='lbfgs', multi_class='ovr').fit(X_train, y_train)

y_pre_test = clf.predict(X_test)
predictions = clf.predict_proba(X_test) 
print('Accuracy is:',clf.score(X_test, y_test))
print(f1_score(y_test, y_pre_test, average='macro'))

Accuracy is: 0.44623655913978494
0.20661297645246463


/Users/apple/venv/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


In [108]:
clf = LogisticRegression(penalty='l1',
                         random_state=0,
                         solver='saga',
                         n_jobs=-1,
                         max_iter=1000,
                         multi_class='ovr').fit(X_train, y_train)

y_pre_test = clf.predict(X_test)
test_prob = clf.predict_proba(X_test)
train_prob = clf.predict_proba(X_train)
print('Accuracy is:',clf.score(X_test, y_test))
print(f1_score(y_test, y_pre_test, average='macro'))

Accuracy is: 0.45698924731182794
0.3523702493828537


/Users/apple/venv/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


#### Decision Tree

In [131]:
X, y = df['commit_message'].values, df['class'].values
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=42)

tf_idf = TfidfVectorizer()
dec_tree = DecisionTreeClassifier(random_state=42, class_weight = 'balanced')

pipeline = Pipeline([('tfidf', tf_idf),('dec', dec_tree)])

param_grid = { #'dec__max_depth': [50, 100, 500, 1000, None],
               #'dec__max_features':[50,None],
               #dec__min_samples_split': [0.5,1.0,10],
               #'dec__min_samples_leaf':[1,3,5],
               #'dec__min_weight_fraction_leaf': [0.0, 0.2,0.5]
              'tfidf__ngram_range':[(1,1),(1,2),(1, 3)],
              'tfidf__max_df':[0.2,0.5,0.8,1.0, None],
              'tfidf__min_df':[0.1, None],
              'tfidf__max_features':[50,100,200,500,None],
              'tfidf__binary':[True, False],
              'tfidf__norm':['l1','l2'],
              'tfidf__use_idf':[True, False],
              'tfidf__smooth_idf':[True, False],
              'tfidf__sublinear_tf':[True, False]
            }

clf = GridSearchCV(pipeline, param_grid = param_grid, cv=10 ,scoring='f1_micro')

clf.fit(X_train, y_train)
y_pred = clf.predict(X_test) 
print(classification_report(y_test, y_pred))

best_parameters = clf.best_estimator_.get_params()
for param_name in sorted(param_grid.keys()):
    print("\t%s: %r" % (param_name, best_parameters[param_name]))

/Users/apple/venv/lib/python3.6/site-packages/sklearn/model_selection/_split.py:657: Warning: The least populated class in y has only 1 members, which is too few. The minimum number of members in any class cannot be less than n_splits=10.
  % (min_groups, self.n_splits)), Warning)


              precision    recall  f1-score   support

         ANT       0.00      0.00      0.00         5
         CLN       0.00      0.00      0.00         6
         CMT       0.00      0.00      0.00         4
         DEL       0.00      0.00      0.00         7
         DOC       0.00      0.00      0.00        13
         DPD       0.00      0.00      0.00         5
         FIX       0.59      0.41      0.49        41
         IMP       0.00      0.00      0.00         1
         MDL       0.00      0.00      0.00         0
         MOD       0.35      0.19      0.24        32
         NFT       0.57      0.24      0.33        51
         RFT       0.00      0.00      0.00         8
         RMN       0.00      0.00      0.00         7
         TST       0.00      0.00      0.00         2
         VER       0.00      0.00      0.00         4

    accuracy                           0.19       186
   macro avg       0.10      0.06      0.07       186
weighted avg       0.35   

/Users/apple/venv/lib/python3.6/site-packages/sklearn/model_selection/_search.py:813: DeprecationWarning: The default of the `iid` parameter will change from True to False in version 0.22 and will be removed in 0.24. This will change numeric results when test-set sizes are unequal.
  DeprecationWarning)
/Users/apple/venv/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/apple/venv/lib/python3.6/site-packages/sklearn/metrics/classification.py:1439: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)


### One VS Rest Binary Classifier

In [56]:
from sklearn.metrics import f1_score
from sklearn.preprocessing import LabelBinarizer
from imblearn.over_sampling import SMOTE
from collections import Counter
from scipy.sparse import csr_matrix

In [44]:
y = df['class'].values
lb = LabelBinarizer()
lb.fit(y)
LabelBinarizer(neg_label=0, pos_label=1, sparse_output=False)
classes = lb.classes_
print(lb.classes_)

y_binary = lb.transform(y)

for index, cl in enumerate(classes):
    df[cl] = y_binary[:,index]

['ANT' 'BRC' 'CLN' 'CMT' 'DEL' 'DOC' 'DPD' 'FIX' 'IMP' 'MDL' 'MOD' 'NFT'
 'RFT' 'RMN' 'TST' 'VER']


In [45]:
df.head()

commit id class                                     commit_message  NFT  \
0   0b9ea98   NFT  add timestampadd timestampdiff function close ...    1   
1   980d9f8   RFT  move code jdbcimplementor jdbcrule new class s...    0   
2   e9d5060   NFT  streamtorel streamtostream join rule transform...    1   
3   a63639b   NFT  add avatica openconnectionrequest goal pass co...    1   
4   a611d64   RMN  reorgan packag structur name convent planner r...    0   

   RFT  RMN  BRC  FIX  CMT  ANT  DEL  MOD  DOC  DPD  VER  CLN  MDL  IMP  TST  
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0  
1    1    0    0    0    0    0    0    0    0    0    0    0    0    0    0  
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0  
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0  
4    0    1    0    0    0    0    0    0    0    0    0    0    0    0    0

In [46]:
df['class'].value_counts()

NFT    276
FIX    193
MOD    156
DOC     53
RFT     43
DEL     41
RMN     37
CLN     31
VER     25
DPD     21
ANT     17
CMT     15
TST      7
IMP      6
BRC      4
MDL      1
Name: class, dtype: int64

In [47]:
for cl in classes:
    print("=================================")
    print('CLASS %s'%cl)
    print(df[cl].value_counts())

CLASS ANT
0    909
1     17
Name: ANT, dtype: int64
CLASS BRC
0    922
1      4
Name: BRC, dtype: int64
CLASS CLN
0    895
1     31
Name: CLN, dtype: int64
CLASS CMT
0    911
1     15
Name: CMT, dtype: int64
CLASS DEL
0    885
1     41
Name: DEL, dtype: int64
CLASS DOC
0    873
1     53
Name: DOC, dtype: int64
CLASS DPD
0    905
1     21
Name: DPD, dtype: int64
CLASS FIX
0    733
1    193
Name: FIX, dtype: int64
CLASS IMP
0    920
1      6
Name: IMP, dtype: int64
CLASS MDL
0    925
1      1
Name: MDL, dtype: int64
CLASS MOD
0    770
1    156
Name: MOD, dtype: int64
CLASS NFT
0    650
1    276
Name: NFT, dtype: int64
CLASS RFT
0    883
1     43
Name: RFT, dtype: int64
CLASS RMN
0    889
1     37
Name: RMN, dtype: int64
CLASS TST
0    919
1      7
Name: TST, dtype: int64
CLASS VER
0    901
1     25
Name: VER, dtype: int64


In [65]:
classes_ = df['class'].value_counts().index
for index, cl in enumerate(classes_):
    print("==============================================")
    print('CLASS %s'%cl)
    print(df[cl].value_counts())
    
    X = csr_matrix.copy(X_tfidf)
    y = df[cl].values
    
    # SMOTE resampling
    try:
        sm = SMOTE(random_state=42,k_neighbors=4)
        X, y = sm.fit_resample(X, y)
        print('Resample Shape')
        print(Counter(y))
    except:
        print('class too imbalance!')
        continue
    
    
    # Split train and test dataset
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)
    
    # Logistic Regression
    clf = LogisticRegression(random_state=42, solver='lbfgs').fit(X_train, y_train)

    y_pred = clf.predict(X_test)
    predictions = clf.predict_proba(X_test) 
    print(clf.score(X_test, y_test))
    print(f1_score(y_test, y_pred, average='macro'))

CLASS NFT
0    650
1    276
Name: NFT, dtype: int64
Resample Shape
Counter({1: 650, 0: 650})
0.8251748251748252
0.8251710253916331
CLASS FIX
0    733
1    193
Name: FIX, dtype: int64
Resample Shape
Counter({0: 733, 1: 733})
0.8202479338842975
0.8185367619490879
CLASS MOD
0    770
1    156
Name: MOD, dtype: int64
Resample Shape
Counter({0: 770, 1: 770})
0.8212180746561886
0.8186988464895628
CLASS DOC
0    873
1     53
Name: DOC, dtype: int64
Resample Shape
Counter({0: 873, 1: 873})
0.9220103986135182
0.9218263107979949
CLASS RFT
0    883
1     43
Name: RFT, dtype: int64
Resample Shape
Counter({0: 883, 1: 883})
0.8936535162950258
0.8932234432234432
CLASS DEL
0    885
1     41
Name: DEL, dtype: int64
Resample Shape
Counter({0: 885, 1: 885})
0.8854700854700854
0.8854366094263793
CLASS RMN
0    889
1     37
Name: RMN, dtype: int64
Resample Shape
Counter({0: 889, 1: 889})
0.9045996592844975
0.9045860907929872
CLASS CLN
0    895
1     31
Name: CLN, dtype: int64
Resample Shape
Counter({0: 895,